# Stochastic volatility 1998

In [3]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

rand_seed = 22101
np.random.seed(rand_seed)

yuima = importr("yuima")
n_stvol_sim_string = """
n_stvol = function(random_seed, num_sim,
                    mu11, mu21, mu22, mu31, mu41, mu42, 
                    sigma11, sigma12, sigma13, sigma14,
                    sigma21, sigma22, sigma23, sigma24,
                    sigma31, sigma32, sigma33, sigma34,
                    sigma41, sigma42, sigma43, sigma44,
                    xinit_vec, vinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11-(1/2)*(v1)^2", "mu21-mu22*v1", "mu31-(1/2)*(v2)^2", "mu41-mu42*v2")
  diffusion = matrix(c("sigma11*v1", "sigma12*v1", "sigma13*v1", "sigma14*v1", 
                       "sigma21", "sigma22", "sigma23", "sigma24", 
                       "sigma31*v2", "sigma32*v2", "sigma33*v2", "sigma34*v2", 
                       "sigma41", "sigma42", "sigma43", "sigma44"), 
                     4, 4, byrow=TRUE)
  
  stvol_model = setModel(drift=drift, diffusion=diffusion,
                          time.variable = "t",
                          state.variable=c("X1", "v1", "X2", "v2"),
                          solve.variable=c("X1", "v1", "X2", "v2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    stvol_sim = simulate(stvol_model, 
                          true.par=list(
                            mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                            sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                            sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                            sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                            sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44), 
                          xinit=c(xinit_vec[[i]][1], vinit_vec[[i]][1], xinit_vec[[i]][2], vinit_vec[[i]][2]), 
                          sampling=newsamp)
    original_data = stvol_sim@data@original.data
    one_sim_stvol = data.frame(original_data[,1], original_data[,3])
    colnames(one_sim_stvol) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_stvol
  }
  return(n_sim_data)
}
"""

n_stvol_sim = SignatureTranslatedAnonymousPackage(n_stvol_sim_string, "n_stvol_sim")
def n_stvol_simulation(random_seed, num_sim,
                        mu11, mu21, mu22, mu31, mu41, mu42, 
                        sigma11, sigma12, sigma13, sigma14,
                        sigma21, sigma22, sigma23, sigma24,
                        sigma31, sigma32, sigma33, sigma34,
                        sigma41, sigma42, sigma43, sigma44,
                        xinit_vec, vinit_vec, T0, T, length):

    n_sim_data = pd.DataFrame(
        n_stvol_sim.n_stvol(random_seed=random_seed, num_sim=num_sim,
                              mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                              sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                              sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                              sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                              sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44,
                              xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)).transpose()
    return n_sim_data


def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return

def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef
    
def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
    autocorr1 = return_series1.apply(lambda x: x.autocorr(lag=1))    
    
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series1.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values
    autocorr2 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(248):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)
    
    
    # adf test on original prices: test if the price difference of the two time series is stationary
    p_values = []
    for i in range(248):
        reg = LinearRegression().fit(np.array(price_series1.iloc[:, i]).reshape((-1, 1)), np.array(price_series2.iloc[:, i]))
        y_pred = reg.predict(np.array(price_series1.iloc[:, i]).reshape((-1, 1)))
        res = np.array(price_series2.iloc[:, i]) - y_pred
        adf_result = adfuller(res)[1]
        p_values.append(adf_result)
    p_values = pd.Series(p_values)
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, 
                               autocorr1, autocorr2, corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3,
                               p_values])
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        'return_autocorrelation1', 'return_autocorrelation2',
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        'price_adf_p_values']
    return stats_data



def loss_function(params):
    
    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)
    
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    n_sim_log_price = n_stvol_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu21=params[1], mu22=params[2], mu31=params[3], mu41=params[4], mu42=params[5],  
        sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
        sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
        sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
        sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
        xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)
    
    n_sim_price = log_price_to_price(n_log_price=n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_return=n_sim_return, n_price=n_sim_price)


    for i in range(n_real_stats.shape[0]):
        for j in range(n_real_stats.shape[1]):
            moment_loss.iloc[i, j] = np.sqrt((n_real_stats.iloc[i, j] - n_sim_stats.iloc[i, j])**2)
    sum_all = np.sum(moment_loss)
    print(sum_all)
    print(np.sum(sum_all))
    print('----------')

    return np.sum(sum_all)



real_price = pd.read_csv("sp500_20180101_20181231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("sp500_20180101_20181231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)


num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]

n_real_stats = real_stats




initial0 = [0.1, 1, 1, 0.1, 1, 1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1]

begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(None, None), (None, None), (None, None), (None, None), (None, None), (None, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)

 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1
[20] 0.1 0.1 0.1

450452
97804
return_mean1                      20.426841
return_mean2                      19.488771
return_sd1                       298.215684
return_sd2                       312.023818
return_skew1                     161.028648
return_skew2                     161.028648
return_kurtosis1                 862.968163
return_kurtosis2                1390.623156
return_autocorrelation1           19.089863
return_autocorrelation2           21.047505
return_correlation_ts1_lag_0     157.643059
return_correlation_ts1_lag_1      19.579955
return_correlation_ts1_lag_2      19.907890
return_correlation_ts1_lag_3      22.509876
return_correlation_ts2_lag_1      20.755811
return_correlation_ts2_lag_2      20.916793
return_correlation_ts2_lag_3      22.260433
price_adf_p_values               100.786508
dtype: float64
3650.3014214377617
----------
 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.

return_mean1                      68.899755
return_mean2                      20.085419
return_sd1                       296.710914
return_sd2                       310.510656
return_skew1                     147.752927
return_skew2                     147.752927
return_kurtosis1                 837.186336
return_kurtosis2                1420.073470
return_autocorrelation1           21.036969
return_autocorrelation2           21.847835
return_correlation_ts1_lag_0     157.644440
return_correlation_ts1_lag_1      20.397024
return_correlation_ts1_lag_2      20.028266
return_correlation_ts1_lag_3      22.500538
return_correlation_ts2_lag_1      21.407643
return_correlation_ts2_lag_2      22.108316
return_correlation_ts2_lag_3      22.439867
price_adf_p_values                77.352705
dtype: float64
3655.736007187373
----------
 [1] -0.4292149  1.0000000  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.100

return_mean1                      45.535430
return_mean2                      20.885215
return_sd1                       295.540628
return_sd2                       309.345670
return_skew1                     157.747881
return_skew2                     157.747881
return_kurtosis1                 846.002986
return_kurtosis2                1374.071000
return_autocorrelation1           21.438314
return_autocorrelation2           19.661974
return_correlation_ts1_lag_0     157.645141
return_correlation_ts1_lag_1      19.971639
return_correlation_ts1_lag_2      19.878525
return_correlation_ts1_lag_3      22.389961
return_correlation_ts2_lag_1      22.297359
return_correlation_ts2_lag_2      19.747715
return_correlation_ts2_lag_3      20.839130
price_adf_p_values                85.158302
dtype: float64
3615.9047493691837
----------
 [1] -0.4277319  1.0000000  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.10

return_mean1                      46.249136
return_mean2                      20.273001
return_sd1                       299.410901
return_sd2                       313.220540
return_skew1                     155.231706
return_skew2                     155.231706
return_kurtosis1                 851.059547
return_kurtosis2                1396.523414
return_autocorrelation1           20.444950
return_autocorrelation2           21.412158
return_correlation_ts1_lag_0     157.644626
return_correlation_ts1_lag_1      20.129216
return_correlation_ts1_lag_2      22.434264
return_correlation_ts1_lag_3      19.894574
return_correlation_ts2_lag_1      20.936351
return_correlation_ts2_lag_2      20.258856
return_correlation_ts2_lag_3      20.894414
price_adf_p_values                80.708405
dtype: float64
3641.9577678121896
----------
 [1] -0.4292149  2.0000000  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.10

return_mean1                     118.909789
return_mean2                      19.768401
return_sd1                        91.855619
return_sd2                       309.929569
return_skew1                     146.638353
return_skew2                     146.638353
return_kurtosis1                 818.671629
return_kurtosis2                1393.567594
return_autocorrelation1           20.944399
return_autocorrelation2           21.698455
return_correlation_ts1_lag_0     155.072170
return_correlation_ts1_lag_1      20.479740
return_correlation_ts1_lag_2      20.400782
return_correlation_ts1_lag_3      20.753353
return_correlation_ts2_lag_1      21.619671
return_correlation_ts2_lag_2      20.641027
return_correlation_ts2_lag_3      21.338916
price_adf_p_values                75.897407
dtype: float64
3444.8252276434882
----------
 [1] -0.4292149  3.2343872  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.10

...

return_mean1                      30.524857
return_mean2                      34.044464
return_sd1                       295.161294
return_sd2                       163.593091
return_skew1                     163.426575
return_skew2                     163.426575
return_kurtosis1                 969.340108
return_kurtosis2                1348.848911
return_autocorrelation1           22.686298
return_autocorrelation2           23.963332
return_correlation_ts1_lag_0      83.013181
return_correlation_ts1_lag_1      21.352497
return_correlation_ts1_lag_2      18.477445
return_correlation_ts1_lag_3      21.442928
return_correlation_ts2_lag_1      21.069742
return_correlation_ts2_lag_2      18.811261
return_correlation_ts2_lag_3      19.209581
price_adf_p_values                80.214724
dtype: float64
3498.6068616504126
----------
 [1]  0.26222544  2.96284705  2.79633061 -0.28927212  0.71695055  4.42044188
 [7]  0.26124088  0.34270097  0.24891787  0.09048606  0.46810189  0.70773396
[13]  0.4

return_mean1                      31.941322
return_mean2                      55.603730
return_sd1                       296.285433
return_sd2                       509.693893
return_skew1                     160.862343
return_skew2                     160.862343
return_kurtosis1                 888.394943
return_kurtosis2                1400.925945
return_autocorrelation1           20.518331
return_autocorrelation2           23.246272
return_correlation_ts1_lag_0      71.714606
return_correlation_ts1_lag_1      19.801103
return_correlation_ts1_lag_2      17.609519
return_correlation_ts1_lag_3      19.373087
return_correlation_ts2_lag_1      20.988485
return_correlation_ts2_lag_2      17.652371
return_correlation_ts2_lag_3      20.258000
price_adf_p_values                72.759927
dtype: float64
3808.4916510376142
----------
 [1]  0.26222544  2.96284705  2.79633061 -0.28927212  0.71695055  4.42044188
 [7]  0.26124088  0.34270097  0.24891787  0.09048606  0.46810189  0.70773396
[13]  0.4

return_mean1                      30.074263
return_mean2                      37.202860
return_sd1                       297.062434
return_sd2                       202.107190
return_skew1                     162.757586
return_skew2                     162.757586
return_kurtosis1                 862.153196
return_kurtosis2                1346.338036
return_autocorrelation1           21.218788
return_autocorrelation2           21.533388
return_correlation_ts1_lag_0      75.307054
return_correlation_ts1_lag_1      18.797221
return_correlation_ts1_lag_2      20.100138
return_correlation_ts1_lag_3      19.956414
return_correlation_ts2_lag_1      20.487585
return_correlation_ts2_lag_2      20.798532
return_correlation_ts2_lag_3      20.279845
price_adf_p_values                86.660307
dtype: float64
3425.5924228566914
----------
 [1]  0.26222544  2.96284705  2.79633061 -0.28927212  0.71695055  4.42044188
 [7]  0.26124088  0.34270097  0.24891787  0.09048606  0.46810189  0.70773396
[13]  0.4

return_mean1                      31.818508
return_mean2                      39.652027
return_sd1                       292.890702
return_sd2                       202.908171
return_skew1                     168.315406
return_skew2                     168.315406
return_kurtosis1                 940.827927
return_kurtosis2                1328.007707
return_autocorrelation1           21.139491
return_autocorrelation2           22.326118
return_correlation_ts1_lag_0      80.015170
return_correlation_ts1_lag_1      19.421177
return_correlation_ts1_lag_2      20.404144
return_correlation_ts1_lag_3      22.796342
return_correlation_ts2_lag_1      22.362433
return_correlation_ts2_lag_2      20.378489
return_correlation_ts2_lag_3      20.533407
price_adf_p_values                80.214129
dtype: float64
3502.326753464023
----------
 [1]  0.26222544  2.96284705  2.79633061 -0.28927212  0.71695055  4.42044188
 [7]  0.26124088  0.34270097  0.24891787  0.09048606  0.46810189  0.70773396
[13]  0.48

return_mean1                      32.291735
return_mean2                      40.891134
return_sd1                       304.155881
return_sd2                       206.364173
return_skew1                     158.082446
return_skew2                     158.082446
return_kurtosis1                 789.008850
return_kurtosis2                1350.783687
return_autocorrelation1           20.100791
return_autocorrelation2           23.419297
return_correlation_ts1_lag_0      81.120732
return_correlation_ts1_lag_1      19.199191
return_correlation_ts1_lag_2      19.050547
return_correlation_ts1_lag_3      21.947088
return_correlation_ts2_lag_1      21.063597
return_correlation_ts2_lag_2      17.989884
return_correlation_ts2_lag_3      21.393272
price_adf_p_values                73.279428
dtype: float64
3358.2241788769693
----------
3358.2241788769693


In [2]:
real_data_folder = "/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_mixed_period/"
real_price = pd.read_csv(real_data_folder + "pair_price_mixed_period_classification.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv(real_data_folder + "pair_return_mixed_period_classification.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)

xinit_vec = []
for i in range(int(real_log_price.shape[1]/2)):
    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
num_sim, T0, T, length = real_stats.shape[0], 0, 0.5, real_price.shape[0]

params = FloatVector(res.x)
print(params)

NameError: name 'pd' is not defined

In [31]:
real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)

xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)
    

n_sim_log_prices = n_stvol_simulation(
    random_seed=9868, num_sim=248,
    mu11=0.26222544, mu21=2.96284705, mu22=2.79633061, 
    mu31=-0.28927212, mu41=0.71695055, mu42=4.42044188,  
    sigma11=0.26124088, sigma12=0.34270097, sigma13=0.24891787, sigma14=0.09048606,
    sigma21=0.46810189, sigma22=0.70773396, sigma23=0.48192585, sigma24=0.81895315,
    sigma31=0.76085335, sigma32=0.26146841, sigma33=0.62789311, sigma34=0.60658349,
    sigma41=0.40349568, sigma42=0.59526509, sigma43=0.15285195, sigma44=0.55066164,
    xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250)

n_sim_pair_prices = log_price_to_price(n_log_price=n_sim_log_prices)
n_sim_pair_returns = price_to_return(n_price=n_sim_pair_prices)

print(n_sim_log_prices)
print(n_sim_pair_prices)
print(n_sim_pair_returns)

n_sim_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_prices.csv")
n_sim_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_returns.csv")


          0         1         2         3         4         5         6    \
0    3.647595  4.134696  4.584573  4.021957  7.338973  5.094021  6.960993   
1    3.649174  4.134583  4.585830  4.022033  7.340594  5.094550  6.962986   
2    3.651029  4.133687  4.585627  4.019790  7.336316  5.086885  6.961123   
3    3.649605  4.129802  4.586812  4.018329  7.338694  5.084848  6.964263   
4    3.650845  4.129692  4.587900  4.016865  7.344219  5.091553  6.964543   
..        ...       ...       ...       ...       ...       ...       ...   
246  4.037186  3.774307  4.739423  3.648087  7.060730  4.382109  6.513901   
247  4.064942  3.777152  4.850469  3.737717  7.066436  4.376049  6.488510   
248  4.128528  3.808291  4.723016  3.635943  7.065330  4.377591  6.501120   
249  4.122496  3.759715  4.758706  3.661737  7.058081  4.384061  6.511247   
250  4.115850  3.784617  4.748819  3.627779  7.066461  4.376874  6.545479   

          7         8         9    ...       486       487       488  \
0  

In [4]:
rand_seed = 22101
np.random.seed(rand_seed)

params = FloatVector(res.x)
n_sim_log_prices = n_stvol_simulation(
    random_seed=9868, num_sim=248,
    mu11=params[0], mu21=params[1], mu22=params[2], 
    mu31=params[3], mu41=params[4], mu42=params[5],  
    sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
    sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
    sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
    sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
    xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250)

n_sim_pair_prices = log_price_to_price(n_log_price=n_sim_log_prices)
n_sim_pair_returns = price_to_return(n_price=n_sim_pair_prices)

print(n_sim_log_prices)
print(n_sim_pair_prices)
print(n_sim_pair_returns)

n_sim_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_prices.csv")
n_sim_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_returns.csv")


          0         1         2         3         4         5         6    \
0    3.719609  4.123019  4.406780  4.090375  7.080876  5.019460  6.978409   
1    3.721237  4.122791  4.408126  4.090504  7.082832  5.020216  6.980586   
2    3.723131  4.121862  4.407723  4.088215  7.078190  5.012388  6.978665   
3    3.721652  4.118098  4.408818  4.086768  7.080728  5.010287  6.981848   
4    3.722815  4.118103  4.409993  4.085308  7.086666  5.017195  6.982111   
..        ...       ...       ...       ...       ...       ...       ...   
246  4.109097  3.762462  4.560978  3.716545  6.801383  4.306889  6.530918   
247  4.136856  3.765307  4.672048  3.806176  6.807097  4.300830  6.505522   
248  4.200445  3.796444  4.544568  3.704401  6.805987  4.302371  6.518134   
249  4.194412  3.747870  4.580265  3.730195  6.798725  4.308839  6.528261   
250  4.187765  3.772771  4.570375  3.696237  6.807125  4.301653  6.562500   

          7         8         9    ...       486       487       488  \
0  

# calibration using 50 real pairs

In [19]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

rand_seed = 22101
np.random.seed(rand_seed)

yuima = importr("yuima")
n_stvol_sim_string = """
n_stvol = function(random_seed, num_sim,
                    mu11, mu21, mu22, mu31, mu41, mu42, 
                    sigma11, sigma12, sigma13, sigma14,
                    sigma21, sigma22, sigma23, sigma24,
                    sigma31, sigma32, sigma33, sigma34,
                    sigma41, sigma42, sigma43, sigma44,
                    xinit_vec, vinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11-(1/2)*(v1)^2", "mu21-mu22*v1", "mu31-(1/2)*(v2)^2", "mu41-mu42*v2")
  diffusion = matrix(c("sigma11*v1", "sigma12*v1", "sigma13*v1", "sigma14*v1", 
                       "sigma21", "sigma22", "sigma23", "sigma24", 
                       "sigma31*v2", "sigma32*v2", "sigma33*v2", "sigma34*v2", 
                       "sigma41", "sigma42", "sigma43", "sigma44"), 
                     4, 4, byrow=TRUE)
  
  stvol_model = setModel(drift=drift, diffusion=diffusion,
                          time.variable = "t",
                          state.variable=c("X1", "v1", "X2", "v2"),
                          solve.variable=c("X1", "v1", "X2", "v2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    stvol_sim = simulate(stvol_model, 
                          true.par=list(
                            mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                            sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                            sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                            sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                            sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44), 
                          xinit=c(xinit_vec[[i]][1], vinit_vec[[i]][1], xinit_vec[[i]][2], vinit_vec[[i]][2]), 
                          sampling=newsamp)
    original_data = stvol_sim@data@original.data
    one_sim_stvol = data.frame(original_data[,1], original_data[,3])
    colnames(one_sim_stvol) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_stvol
  }
  return(n_sim_data)
}
"""

n_stvol_sim = SignatureTranslatedAnonymousPackage(n_stvol_sim_string, "n_stvol_sim")
def n_stvol_simulation(random_seed, num_sim,
                        mu11, mu21, mu22, mu31, mu41, mu42, 
                        sigma11, sigma12, sigma13, sigma14,
                        sigma21, sigma22, sigma23, sigma24,
                        sigma31, sigma32, sigma33, sigma34,
                        sigma41, sigma42, sigma43, sigma44,
                        xinit_vec, vinit_vec, T0, T, length):

    n_sim_data = pd.DataFrame(
        n_stvol_sim.n_stvol(random_seed=random_seed, num_sim=num_sim,
                              mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                              sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                              sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                              sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                              sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44,
                              xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)).transpose()
    return n_sim_data


def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return

def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef
    
def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
    autocorr1 = return_series1.apply(lambda x: x.autocorr(lag=1))    
    
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series1.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values
    autocorr2 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)
    
    
    # adf test on original prices: test if the price difference of the two time series is stationary
    p_values = []
    for i in range(int(real_price.shape[1]/2)):
        reg = LinearRegression().fit(np.array(price_series1.iloc[:, i]).reshape((-1, 1)), np.array(price_series2.iloc[:, i]))
        y_pred = reg.predict(np.array(price_series1.iloc[:, i]).reshape((-1, 1)))
        res = np.array(price_series2.iloc[:, i]) - y_pred
        adf_result = adfuller(res)[1]
        p_values.append(adf_result)
    p_values = pd.Series(p_values)
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, 
                               autocorr1, autocorr2, corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3,
                               p_values])
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        'return_autocorrelation1', 'return_autocorrelation2',
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        'price_adf_p_values']
    return stats_data



def loss_function(params):
    
    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)
    
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    n_sim_log_price = n_stvol_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu21=params[1], mu22=params[2], mu31=params[3], mu41=params[4], mu42=params[5],  
        sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
        sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
        sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
        sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
        xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)
    
    n_sim_price = log_price_to_price(n_log_price=n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_return=n_sim_return, n_price=n_sim_price)


    for i in range(n_real_stats.shape[0]):
        for j in range(n_real_stats.shape[1]):
            moment_loss.iloc[i, j] = np.sqrt((n_real_stats.iloc[i, j] - n_sim_stats.iloc[i, j])**2)
    sum_all = np.sum(moment_loss)
    print(sum_all)
    print(np.sum(sum_all))
    print('----------')

    return np.sum(sum_all)



real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20180101_20181231/calibration_50_pairs_prices_2018.csv", 
                         index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20180101_20181231/calibration_50_pairs_returns_2018.csv", 
                          index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)


num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]

n_real_stats = real_stats




initial0 = [0.1, 1, 1, 0.1, 1, 1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1]

begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(None, None), (None, None), (None, None), (None, None), (None, None), (None, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)

 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1
[20] 0.1 0.1 0.1

450452
97804
return_mean1                      4.269426
return_mean2                      4.454564
return_sd1                       54.605577
return_sd2                       63.853802
return_skew1                     29.170595
return_skew2                     29.170595
return_kurtosis1                151.451217
return_kurtosis2                332.632602
return_autocorrelation1           3.471443
return_autocorrelation2           3.604820
return_correlation_ts1_lag_0     31.182532
return_correlation_ts1_lag_1      3.188766
return_correlation_ts1_lag_2      4.615300
return_correlation_ts1_lag_3      4.448960
return_correlation_ts2_lag_1      4.060288
return_correlation_ts2_lag_2      3.933318
return_correlation_ts2_lag_3      4.957503
price_adf_p_values               20.729384
dtype: float64
753.8006915884282
----------
 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0

return_mean1                      5.879157
return_mean2                      4.528293
return_sd1                       54.363148
return_sd2                       63.608547
return_skew1                     34.608330
return_skew2                     34.608330
return_kurtosis1                143.082477
return_kurtosis2                332.898598
return_autocorrelation1           3.690329
return_autocorrelation2           3.396069
return_correlation_ts1_lag_0     31.183049
return_correlation_ts1_lag_1      3.888639
return_correlation_ts1_lag_2      4.235849
return_correlation_ts1_lag_3      4.481549
return_correlation_ts2_lag_1      3.572673
return_correlation_ts2_lag_2      3.798603
return_correlation_ts2_lag_3      4.071224
price_adf_p_values               15.485989
dtype: float64
751.3808522774821
----------
 [1] -0.2151432  1.0000000  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.1000000  0.1000000  0

return_mean1                      5.747872
return_mean2                      4.704001
return_sd1                       54.209490
return_sd2                       63.455712
return_skew1                     29.435158
return_skew2                     29.435158
return_kurtosis1                154.648963
return_kurtosis2                328.824965
return_autocorrelation1           4.833391
return_autocorrelation2           4.753607
return_correlation_ts1_lag_0     31.182984
return_correlation_ts1_lag_1      4.783804
return_correlation_ts1_lag_2      4.055213
return_correlation_ts1_lag_3      4.000257
return_correlation_ts2_lag_1      4.672234
return_correlation_ts2_lag_2      4.351744
return_correlation_ts2_lag_3      4.369775
price_adf_p_values               14.142300
dtype: float64
751.6066290497772
----------
 [1] -0.215578  2.000000  1.000000  0.100000  1.000000  1.000000  0.100000
 [8]  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000
[15]  0.100000  0.100000  0.1000

return_mean1                      7.128078
return_mean2                      4.616984
return_sd1                       39.708066
return_sd2                       62.739790
return_skew1                     31.693133
return_skew2                     31.693133
return_kurtosis1                150.202471
return_kurtosis2                342.748624
return_autocorrelation1           3.669198
return_autocorrelation2           4.123539
return_correlation_ts1_lag_0     31.092109
return_correlation_ts1_lag_1      3.733117
return_correlation_ts1_lag_2      4.798435
return_correlation_ts1_lag_3      4.039572
return_correlation_ts2_lag_1      4.490136
return_correlation_ts2_lag_2      3.840789
return_correlation_ts2_lag_3      4.193795
price_adf_p_values               12.856761
dtype: float64
747.3677308938023
----------
 [1] -0.215578  1.654994  1.000000  0.100000  1.000000  1.000000  0.100000
 [8]  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000
[15]  0.100000  0.100000  0.1000

return_mean1                      7.896839
return_mean2                      4.940074
return_sd1                       38.392156
return_sd2                       63.629778
return_skew1                     29.036479
return_skew2                     29.036479
return_kurtosis1                148.195078
return_kurtosis2                324.362927
return_autocorrelation1           3.609135
return_autocorrelation2           3.478830
return_correlation_ts1_lag_0     31.073346
return_correlation_ts1_lag_1      3.763485
return_correlation_ts1_lag_2      4.014396
return_correlation_ts1_lag_3      4.241934
return_correlation_ts2_lag_1      4.352958
return_correlation_ts2_lag_2      4.343103
return_correlation_ts2_lag_3      4.091156
price_adf_p_values               14.373364
dtype: float64
722.8315173445042
----------
 [1] -0.215578  1.618821  1.000000  0.100000  1.000000  1.000000  0.100000
 [8]  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000
[15]  0.100000  0.100000  0.1000

...

return_mean1                     15.810641
return_mean2                     21.356194
return_sd1                      196.348431
return_sd2                      216.946675
return_skew1                     30.579657
return_skew2                     30.579657
return_kurtosis1                191.403354
return_kurtosis2                338.747130
return_autocorrelation1           4.115461
return_autocorrelation2           4.833200
return_correlation_ts1_lag_0     23.728484
return_correlation_ts1_lag_1      4.342228
return_correlation_ts1_lag_2      4.346293
return_correlation_ts1_lag_3      3.771804
return_correlation_ts2_lag_1      4.820873
return_correlation_ts2_lag_2      4.723737
return_correlation_ts2_lag_3      4.319424
price_adf_p_values               18.866909
dtype: float64
1119.64015374705
----------
 [1] -0.2864057  1.6280840  2.3215833  1.4146118  0.3093665 -0.2152386
 [7]  0.2778213  0.4131915  0.4343720  0.8368465  0.5838001  0.7503454
[13]  1.1070087  0.7832930  0.4061488  0.

return_mean1                     12.818326
return_mean2                     17.118910
return_sd1                      149.347430
return_sd2                      200.168496
return_skew1                     28.770690
return_skew2                     28.770690
return_kurtosis1                148.341109
return_kurtosis2                331.843773
return_autocorrelation1           5.160657
return_autocorrelation2           4.719688
return_correlation_ts1_lag_0     18.872155
return_correlation_ts1_lag_1      4.299637
return_correlation_ts1_lag_2      3.564003
return_correlation_ts1_lag_3      4.044601
return_correlation_ts2_lag_1      4.162559
return_correlation_ts2_lag_2      3.434404
return_correlation_ts2_lag_3      4.601692
price_adf_p_values               14.381890
dtype: float64
984.4207104812087
----------
 [1] -0.2864057  1.6280840  2.3215833  1.4146118  0.3093665 -0.2152386
 [7]  0.2778213  0.4131915  0.4343720  0.8368465  0.5838001  0.7503454
[13]  1.1070087  0.7832930  0.4061488  0

return_mean1                     15.653075
return_mean2                     22.264030
return_sd1                      186.846499
return_sd2                      232.635816
return_skew1                     32.855005
return_skew2                     32.855005
return_kurtosis1                133.626323
return_kurtosis2                332.194830
return_autocorrelation1           3.702318
return_autocorrelation2           3.946653
return_correlation_ts1_lag_0     19.941805
return_correlation_ts1_lag_1      3.981356
return_correlation_ts1_lag_2      3.986306
return_correlation_ts1_lag_3      3.955512
return_correlation_ts2_lag_1      3.636310
return_correlation_ts2_lag_2      3.723914
return_correlation_ts2_lag_3      4.003309
price_adf_p_values               16.004413
dtype: float64
1055.8124796744492
----------
 [1] -0.2864057  1.6280840  2.3215833  1.4146118  0.3093665 -0.2152386
 [7]  0.2778213  0.4131915  0.4343720  0.8368465  0.5838001  0.7503454
[13]  1.1070087  0.7832930  0.4061488  

return_mean1                     16.457486
return_mean2                     17.439018
return_sd1                      180.456985
return_sd2                      179.960867
return_skew1                     34.458279
return_skew2                     34.458279
return_kurtosis1                189.485693
return_kurtosis2                325.127063
return_autocorrelation1           3.941990
return_autocorrelation2           4.197450
return_correlation_ts1_lag_0     21.847278
return_correlation_ts1_lag_1      4.164299
return_correlation_ts1_lag_2      5.077654
return_correlation_ts1_lag_3      3.397373
return_correlation_ts2_lag_1      4.005035
return_correlation_ts2_lag_2      3.256667
return_correlation_ts2_lag_3      4.042785
price_adf_p_values               16.489821
dtype: float64
1048.26402010469
----------
 [1] -0.2864057  1.6280840  2.3215833  1.4146118  0.3093665 -0.2152386
 [7]  0.2778213  0.4131915  0.4343720  0.8368465  0.5838001  0.7503454
[13]  1.1070087  0.7832930  0.4061488  0.

return_mean1                     15.752350
return_mean2                     18.055559
return_sd1                      136.911744
return_sd2                      153.430488
return_skew1                     33.469078
return_skew2                     33.469078
return_kurtosis1                160.503054
return_kurtosis2                347.925416
return_autocorrelation1           4.962253
return_autocorrelation2           4.497390
return_correlation_ts1_lag_0     18.914095
return_correlation_ts1_lag_1      4.089661
return_correlation_ts1_lag_2      4.328893
return_correlation_ts1_lag_3      3.499886
return_correlation_ts2_lag_1      4.328757
return_correlation_ts2_lag_2      4.011866
return_correlation_ts2_lag_3      4.012599
price_adf_p_values               15.187599
dtype: float64
967.3497683353344
----------
 [1] -0.2864057  1.6280840  2.3215833  1.4146118  0.3093665 -0.2152386
 [7]  0.2778213  0.4131915  0.4343720  0.8368465  0.5838001  0.7503454
[13]  1.1070087  0.7832930  0.4061488  0

In [18]:
real_price.shape[1]/2


50.0

In [13]:
print(real_price)
num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]
int(num_sim/2)

124

In [25]:
real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)

xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)

    
    
params = FloatVector((
    -0.2864057, 1.6280840, 2.3215833, 1.4146118, 0.3093665, -0.2152386,
    0.2778213,  0.4131915, 0.4343720, 0.8368465, 
    0.5838001, 0.7503454, 1.1070087, 0.7832930, 
    0.4061488, 0.3638802, 0.4579273, 0.4637746,
    0.3959352, 0.4272114, 1.2017875, 0.9577078))

    
n_sim_log_prices = n_stvol_simulation(
    random_seed=9868, num_sim=248,
    mu11=params[0], mu21=params[1], mu22=params[2], 
    mu31=params[3], mu41=params[4], mu42=params[5],  
    sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
    sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
    sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
    sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
    xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250)

n_sim_pair_prices = log_price_to_price(n_log_price=n_sim_log_prices)
n_sim_pair_returns = price_to_return(n_price=n_sim_pair_prices)

print(n_sim_log_prices)
print(n_sim_pair_prices)
print(n_sim_pair_returns)

n_sim_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_prices.csv")
n_sim_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_returns.csv")



          0         1         2         3         4         5         6    \
0    3.647595  4.134696  4.584573  4.021957  7.338973  5.094021  6.960993   
1    3.646166  4.140884  4.583492  4.028096  7.339014  5.100756  6.961025   
2    3.644825  4.147544  4.580023  4.030036  7.331266  5.096052  6.960149   
3    3.637309  4.150289  4.577869  4.035444  7.327955  5.100455  6.948700   
4    3.634483  4.155610  4.576780  4.042049  7.328436  5.105969  6.943158   
..        ...       ...       ...       ...       ...       ...       ...   
246  2.681987  4.794032  3.748867  4.592954  6.565727  6.493952  6.016957   
247  2.672417  4.797838  3.941857  4.658696  6.548535  6.412239  5.984323   
248  2.679089  4.796615  3.725764  4.574196  6.548937  6.440993  5.990832   
249  2.606974  4.808985  3.754484  4.593163  6.618206  6.662892  5.955499   
250  2.657940  4.808704  3.745634  4.589896  6.603059  6.556672  5.961294   

          7         8         9    ...       486       487       488  \
0  

In [ ]:
random_seed=9868, num_sim=248,
mu11=0.26222544, mu21=2.96284705, mu22=2.79633061, 
mu31=-0.28927212, mu41=0.71695055, mu42=4.42044188,  
sigma11=0.26124088, sigma12=0.34270097, sigma13=0.24891787, sigma14=0.09048606,
sigma21=0.46810189, sigma22=0.70773396, sigma23=0.48192585, sigma24=0.81895315,
sigma31=0.76085335, sigma32=0.26146841, sigma33=0.62789311, sigma34=0.60658349,
sigma41=0.40349568, sigma42=0.59526509, sigma43=0.15285195, sigma44=0.55066164,
xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250

# ou as volatility params positive

In [20]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

rand_seed = 22101
np.random.seed(rand_seed)

yuima = importr("yuima")
n_stvol_sim_string = """
n_stvol = function(random_seed, num_sim,
                    mu11, mu21, mu22, mu31, mu41, mu42, 
                    sigma11, sigma12, sigma13, sigma14,
                    sigma21, sigma22, sigma23, sigma24,
                    sigma31, sigma32, sigma33, sigma34,
                    sigma41, sigma42, sigma43, sigma44,
                    xinit_vec, vinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11-(1/2)*(v1)^2", "mu21-mu22*v1", "mu31-(1/2)*(v2)^2", "mu41-mu42*v2")
  diffusion = matrix(c("sigma11*v1", "sigma12*v1", "sigma13*v1", "sigma14*v1", 
                       "sigma21", "sigma22", "sigma23", "sigma24", 
                       "sigma31*v2", "sigma32*v2", "sigma33*v2", "sigma34*v2", 
                       "sigma41", "sigma42", "sigma43", "sigma44"), 
                     4, 4, byrow=TRUE)
  
  stvol_model = setModel(drift=drift, diffusion=diffusion,
                          time.variable = "t",
                          state.variable=c("X1", "v1", "X2", "v2"),
                          solve.variable=c("X1", "v1", "X2", "v2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    stvol_sim = simulate(stvol_model, 
                          true.par=list(
                            mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                            sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                            sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                            sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                            sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44), 
                          xinit=c(xinit_vec[[i]][1], vinit_vec[[i]][1], xinit_vec[[i]][2], vinit_vec[[i]][2]), 
                          sampling=newsamp)
    original_data = stvol_sim@data@original.data
    one_sim_stvol = data.frame(original_data[,1], original_data[,3])
    colnames(one_sim_stvol) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_stvol
  }
  return(n_sim_data)
}
"""

n_stvol_sim = SignatureTranslatedAnonymousPackage(n_stvol_sim_string, "n_stvol_sim")
def n_stvol_simulation(random_seed, num_sim,
                        mu11, mu21, mu22, mu31, mu41, mu42, 
                        sigma11, sigma12, sigma13, sigma14,
                        sigma21, sigma22, sigma23, sigma24,
                        sigma31, sigma32, sigma33, sigma34,
                        sigma41, sigma42, sigma43, sigma44,
                        xinit_vec, vinit_vec, T0, T, length):

    n_sim_data = pd.DataFrame(
        n_stvol_sim.n_stvol(random_seed=random_seed, num_sim=num_sim,
                              mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                              sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                              sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                              sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                              sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44,
                              xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)).transpose()
    return n_sim_data


def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return

def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef
    
def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
    autocorr1 = return_series1.apply(lambda x: x.autocorr(lag=1))    
    
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series1.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values
    autocorr2 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)
    
    
    # adf test on original prices: test if the price difference of the two time series is stationary
    p_values = []
    for i in range(int(real_price.shape[1]/2)):
        reg = LinearRegression().fit(np.array(price_series1.iloc[:, i]).reshape((-1, 1)), np.array(price_series2.iloc[:, i]))
        y_pred = reg.predict(np.array(price_series1.iloc[:, i]).reshape((-1, 1)))
        res = np.array(price_series2.iloc[:, i]) - y_pred
        adf_result = adfuller(res)[1]
        p_values.append(adf_result)
    p_values = pd.Series(p_values)
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, 
                               autocorr1, autocorr2, corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3,
                               p_values])
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        'return_autocorrelation1', 'return_autocorrelation2',
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        'price_adf_p_values']
    return stats_data



def loss_function(params):
    
    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)
    
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    n_sim_log_price = n_stvol_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu21=params[1], mu22=params[2], mu31=params[3], mu41=params[4], mu42=params[5],  
        sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
        sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
        sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
        sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
        xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)
    
    n_sim_price = log_price_to_price(n_log_price=n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_return=n_sim_return, n_price=n_sim_price)


    for i in range(n_real_stats.shape[0]):
        for j in range(n_real_stats.shape[1]):
            moment_loss.iloc[i, j] = np.sqrt((n_real_stats.iloc[i, j] - n_sim_stats.iloc[i, j])**2)
    sum_all = np.sum(moment_loss)
    print(sum_all)
    print(np.sum(sum_all))
    print('----------')

    return np.sum(sum_all)



real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20180101_20181231/calibration_50_pairs_prices_2018.csv", 
                         index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20180101_20181231/calibration_50_pairs_returns_2018.csv", 
                          index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)


num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]

n_real_stats = real_stats




initial0 = [0.1, 1, 1, 0.1, 1, 1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1]

begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(None, None), (0, None), (0, None), (None, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)

 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1
[20] 0.1 0.1 0.1

450452
97804
return_mean1                      4.269426
return_mean2                      4.454564
return_sd1                       54.605577
return_sd2                       63.853802
return_skew1                     29.170595
return_skew2                     29.170595
return_kurtosis1                151.451217
return_kurtosis2                332.632602
return_autocorrelation1           3.471443
return_autocorrelation2           3.604820
return_correlation_ts1_lag_0     31.182532
return_correlation_ts1_lag_1      3.188766
return_correlation_ts1_lag_2      4.615300
return_correlation_ts1_lag_3      4.448960
return_correlation_ts2_lag_1      4.060288
return_correlation_ts2_lag_2      3.933318
return_correlation_ts2_lag_3      4.957503
price_adf_p_values               20.729384
dtype: float64
753.8006915884282
----------
 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0

return_mean1                      5.879157
return_mean2                      4.528293
return_sd1                       54.363148
return_sd2                       63.608547
return_skew1                     34.608330
return_skew2                     34.608330
return_kurtosis1                143.082477
return_kurtosis2                332.898598
return_autocorrelation1           3.690329
return_autocorrelation2           3.396069
return_correlation_ts1_lag_0     31.183049
return_correlation_ts1_lag_1      3.888639
return_correlation_ts1_lag_2      4.235849
return_correlation_ts1_lag_3      4.481549
return_correlation_ts2_lag_1      3.572673
return_correlation_ts2_lag_2      3.798603
return_correlation_ts2_lag_3      4.071224
price_adf_p_values               15.485989
dtype: float64
751.3808522774821
----------
 [1] -0.2151432  1.0000000  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.1000000  0.1000000  0

return_mean1                      6.007062
return_mean2                      4.704001
return_sd1                       51.300774
return_sd2                       63.455712
return_skew1                     29.267602
return_skew2                     29.267602
return_kurtosis1                153.855599
return_kurtosis2                328.824965
return_autocorrelation1           4.849855
return_autocorrelation2           4.753607
return_correlation_ts1_lag_0     31.176079
return_correlation_ts1_lag_1      4.782012
return_correlation_ts1_lag_2      4.040292
return_correlation_ts1_lag_3      3.989361
return_correlation_ts2_lag_1      4.676783
return_correlation_ts2_lag_2      4.347831
return_correlation_ts2_lag_3      4.360846
price_adf_p_values               14.034318
dtype: float64
747.6943008895993
----------
 [1] -0.215578  1.793574  1.000000  0.100000  1.000000  1.000000  0.100000
 [8]  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000
[15]  0.100000  0.100000  0.1000

return_mean1                     17.358828
return_mean2                      4.616984
return_sd1                       11.813484
return_sd2                       62.739790
return_skew1                     29.795688
return_skew2                     29.795688
return_kurtosis1                146.072656
return_kurtosis2                342.748624
return_autocorrelation1           3.723387
return_autocorrelation2           4.123539
return_correlation_ts1_lag_0     30.714053
return_correlation_ts1_lag_1      3.701513
return_correlation_ts1_lag_2      4.744142
return_correlation_ts1_lag_3      4.010503
return_correlation_ts2_lag_1      4.492789
return_correlation_ts2_lag_2      3.853177
return_correlation_ts2_lag_3      4.162995
price_adf_p_values               12.971580
dtype: float64
721.4394230532483
----------
 [1] -0.215578  2.983021  1.000000  0.100000  1.000000  1.000000  0.100000
 [8]  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000
[15]  0.100000  0.100000  0.1000

return_mean1                     17.914759
return_mean2                      4.940074
return_sd1                       12.459987
return_sd2                       63.629778
return_skew1                     27.896052
return_skew2                     27.896052
return_kurtosis1                149.581579
return_kurtosis2                324.362927
return_autocorrelation1           3.721654
return_autocorrelation2           3.478830
return_correlation_ts1_lag_0     30.710260
return_correlation_ts1_lag_1      3.759230
return_correlation_ts1_lag_2      3.971291
return_correlation_ts1_lag_3      4.266619
return_correlation_ts2_lag_1      4.315655
return_correlation_ts2_lag_2      4.330547
return_correlation_ts2_lag_3      4.084507
price_adf_p_values               14.451589
dtype: float64
705.7713922264171
----------
 [1] -0.215578  2.944177  1.000000  0.100000  1.000000  1.000000  0.100000
 [8]  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000  0.100000
[15]  0.100000  0.100000  0.1000

...

return_mean1                     12.807218
return_mean2                     10.472995
return_sd1                      138.033802
return_sd2                      119.670948
return_skew1                     32.283419
return_skew2                     32.283419
return_kurtosis1                160.909866
return_kurtosis2                331.208979
return_autocorrelation1           4.521167
return_autocorrelation2           5.062033
return_correlation_ts1_lag_0     21.022885
return_correlation_ts1_lag_1      4.819863
return_correlation_ts1_lag_2      4.223991
return_correlation_ts1_lag_3      4.765270
return_correlation_ts2_lag_1      4.064808
return_correlation_ts2_lag_2      3.372436
return_correlation_ts2_lag_3      5.219208
price_adf_p_values               17.664995
dtype: float64
912.4073024923899
----------
 [1] 0.1369711 2.2903719 1.5068982 0.1357925 2.5472804 3.9497748 0.1687479
 [8] 0.3148438 0.2397902 0.3666652 1.4863637 1.1394869 0.4210796 0.3974794
[15] 0.1462609 0.2563539 0.33291

return_mean1                     12.817238
return_mean2                      9.337877
return_sd1                      108.498706
return_sd2                      104.864144
return_skew1                     28.806415
return_skew2                     28.806415
return_kurtosis1                166.736409
return_kurtosis2                322.974532
return_autocorrelation1           3.453918
return_autocorrelation2           3.482543
return_correlation_ts1_lag_0     20.009799
return_correlation_ts1_lag_1      3.973261
return_correlation_ts1_lag_2      4.138484
return_correlation_ts1_lag_3      3.823948
return_correlation_ts2_lag_1      3.443780
return_correlation_ts2_lag_2      3.339598
return_correlation_ts2_lag_3      4.443174
price_adf_p_values               18.926775
dtype: float64
851.8770150876793
----------
 [1] 0.1369711 2.2903719 1.5068982 0.1357925 2.5472804 3.9497748 0.1687479
 [8] 0.3148438 0.2397902 0.3666652 1.4863637 1.1394869 0.4210796 0.3974794
[15] 0.1462609 0.2563539 0.33291

return_mean1                     15.196289
return_mean2                     11.317158
return_sd1                      148.678918
return_sd2                      135.381822
return_skew1                     34.303390
return_skew2                     34.303390
return_kurtosis1                159.776449
return_kurtosis2                331.350138
return_autocorrelation1           3.787631
return_autocorrelation2           4.601074
return_correlation_ts1_lag_0     22.064446
return_correlation_ts1_lag_1      3.979097
return_correlation_ts1_lag_2      4.099401
return_correlation_ts1_lag_3      3.929493
return_correlation_ts2_lag_1      4.404090
return_correlation_ts2_lag_2      3.354628
return_correlation_ts2_lag_3      3.644680
price_adf_p_values               14.225802
dtype: float64
938.3978970993385
----------
 [1] 0.1369711 2.2903719 1.5068982 0.1357925 2.5472804 3.9497748 0.1687479
 [8] 0.3148438 0.2397902 0.3666652 1.4863637 1.1394869 0.4210796 0.3974794
[15] 0.1462609 0.2563539 0.33291

return_mean1                     13.804296
return_mean2                      9.495512
return_sd1                      126.421949
return_sd2                      123.128951
return_skew1                     27.919769
return_skew2                     27.919769
return_kurtosis1                172.386726
return_kurtosis2                315.077680
return_autocorrelation1           5.145369
return_autocorrelation2           4.414878
return_correlation_ts1_lag_0     19.194698
return_correlation_ts1_lag_1      4.044665
return_correlation_ts1_lag_2      4.923493
return_correlation_ts1_lag_3      4.120728
return_correlation_ts2_lag_1      3.702097
return_correlation_ts2_lag_2      3.378659
return_correlation_ts2_lag_3      3.448892
price_adf_p_values               15.537274
dtype: float64
884.0654074026037
----------
 [1] 0.1369711 2.2903719 1.5068982 0.1357925 2.5472804 3.9497748 0.1687479
 [8] 0.3148438 0.2397902 0.3666652 1.4863637 1.1394869 0.4210796 0.3974794
[15] 0.1462609 0.2563539 0.33291

return_mean1                     12.832213
return_mean2                      9.090500
return_sd1                      117.683825
return_sd2                      103.474948
return_skew1                     30.954258
return_skew2                     30.954258
return_kurtosis1                161.301302
return_kurtosis2                323.990285
return_autocorrelation1           3.979206
return_autocorrelation2           4.505540
return_correlation_ts1_lag_0     19.699243
return_correlation_ts1_lag_1      4.227854
return_correlation_ts1_lag_2      4.835332
return_correlation_ts1_lag_3      4.365533
return_correlation_ts2_lag_1      4.180438
return_correlation_ts2_lag_2      3.591732
return_correlation_ts2_lag_3      4.378465
price_adf_p_values               12.128673
dtype: float64
856.1736067592079
----------
 [1] 0.1369711 2.2903719 1.5068982 0.1357925 2.5472804 3.9497748 0.1687479
 [8] 0.3148438 0.2397902 0.3666652 1.4863637 1.1394869 0.4210796 0.3974794
[15] 0.1462609 0.2563539 0.33291

In [23]:
params = (res.x)
print(params)

[0.13697113 2.29037194 1.50689817 0.1357925  2.54728038 3.94977484
 0.16874789 0.31484381 0.23979018 0.36666522 1.48636367 1.13948693
 0.4210796  0.39747944 0.14626087 0.2563539  0.33291269 0.71427515
 0.48158734 1.14787531 1.05066798 1.07479698]


In [24]:
real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)

xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)

    
    
params = FloatVector((
    0.13697113, 2.29037194, 1.50689817, 0.1357925,  2.54728038, 3.94977484,
    0.16874789, 0.31484381, 0.23979018, 0.36666522, 
    1.48636367, 1.13948693, 0.4210796,  0.39747944, 
    0.14626087, 0.2563539,  0.33291269, 0.71427515,
    0.48158734, 1.14787531, 1.05066798, 1.07479698))

    
n_sim_log_prices = n_stvol_simulation(
    random_seed=9868, num_sim=248,
    mu11=params[0], mu21=params[1], mu22=params[2], 
    mu31=params[3], mu41=params[4], mu42=params[5],  
    sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
    sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
    sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
    sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
    xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250)

n_sim_pair_prices = log_price_to_price(n_log_price=n_sim_log_prices)
n_sim_pair_returns = price_to_return(n_price=n_sim_pair_prices)

print(n_sim_log_prices)
print(n_sim_pair_prices)
print(n_sim_pair_returns)

n_sim_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_prices.csv")
n_sim_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_returns.csv")




          0         1         2         3         4         5         6    \
0    3.647595  4.134696  4.584573  4.021957  7.338973  5.094021  6.960993   
1    3.648149  4.134752  4.585131  4.022486  7.340130  5.095382  6.962320   
2    3.649856  4.134635  4.582862  4.022546  7.336252  5.092690  6.961665   
3    3.641709  4.131643  4.583433  4.020604  7.336799  5.090316  6.961540   
4    3.638590  4.132183  4.582924  4.021208  7.340651  5.092574  6.961141   
..        ...       ...       ...       ...       ...       ...       ...   
246  2.518527  3.441151  4.144111  3.643607  6.700365  4.537156  6.035745   
247  2.515770  3.426951  4.348229  3.793273  6.707813  4.530348  5.999589   
248  2.562028  3.415592  4.119902  3.622707  6.707377  4.531506  6.008968   
249  2.447081  3.358916  4.155924  3.636168  6.673512  4.563789  5.985920   
250  2.485727  3.403746  4.150883  3.629453  6.683301  4.561153  6.004502   

          7         8         9    ...       486       487       488  \
0  

# calibration using 100 real pairs

In [26]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

rand_seed = 22101
np.random.seed(rand_seed)

yuima = importr("yuima")
n_stvol_sim_string = """
n_stvol = function(random_seed, num_sim,
                    mu11, mu21, mu22, mu31, mu41, mu42, 
                    sigma11, sigma12, sigma13, sigma14,
                    sigma21, sigma22, sigma23, sigma24,
                    sigma31, sigma32, sigma33, sigma34,
                    sigma41, sigma42, sigma43, sigma44,
                    xinit_vec, vinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11-(1/2)*(v1)^2", "mu21-mu22*v1", "mu31-(1/2)*(v2)^2", "mu41-mu42*v2")
  diffusion = matrix(c("sigma11*v1", "sigma12*v1", "sigma13*v1", "sigma14*v1", 
                       "sigma21", "sigma22", "sigma23", "sigma24", 
                       "sigma31*v2", "sigma32*v2", "sigma33*v2", "sigma34*v2", 
                       "sigma41", "sigma42", "sigma43", "sigma44"), 
                     4, 4, byrow=TRUE)
  
  stvol_model = setModel(drift=drift, diffusion=diffusion,
                          time.variable = "t",
                          state.variable=c("X1", "v1", "X2", "v2"),
                          solve.variable=c("X1", "v1", "X2", "v2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    stvol_sim = simulate(stvol_model, 
                          true.par=list(
                            mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                            sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                            sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                            sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                            sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44), 
                          xinit=c(xinit_vec[[i]][1], vinit_vec[[i]][1], xinit_vec[[i]][2], vinit_vec[[i]][2]), 
                          sampling=newsamp)
    original_data = stvol_sim@data@original.data
    one_sim_stvol = data.frame(original_data[,1], original_data[,3])
    colnames(one_sim_stvol) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_stvol
  }
  return(n_sim_data)
}
"""

n_stvol_sim = SignatureTranslatedAnonymousPackage(n_stvol_sim_string, "n_stvol_sim")
def n_stvol_simulation(random_seed, num_sim,
                        mu11, mu21, mu22, mu31, mu41, mu42, 
                        sigma11, sigma12, sigma13, sigma14,
                        sigma21, sigma22, sigma23, sigma24,
                        sigma31, sigma32, sigma33, sigma34,
                        sigma41, sigma42, sigma43, sigma44,
                        xinit_vec, vinit_vec, T0, T, length):

    n_sim_data = pd.DataFrame(
        n_stvol_sim.n_stvol(random_seed=random_seed, num_sim=num_sim,
                              mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                              sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                              sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                              sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                              sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44,
                              xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)).transpose()
    return n_sim_data


def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return

def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef
    
def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
    autocorr1 = return_series1.apply(lambda x: x.autocorr(lag=1))    
    
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series1.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values
    autocorr2 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(int(real_price.shape[1]/2)):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)
    
    
    # adf test on original prices: test if the price difference of the two time series is stationary
    p_values = []
    for i in range(int(real_price.shape[1]/2)):
        reg = LinearRegression().fit(np.array(price_series1.iloc[:, i]).reshape((-1, 1)), np.array(price_series2.iloc[:, i]))
        y_pred = reg.predict(np.array(price_series1.iloc[:, i]).reshape((-1, 1)))
        res = np.array(price_series2.iloc[:, i]) - y_pred
        adf_result = adfuller(res)[1]
        p_values.append(adf_result)
    p_values = pd.Series(p_values)
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, 
                               autocorr1, autocorr2, corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3,
                               p_values])
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        'return_autocorrelation1', 'return_autocorrelation2',
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        'price_adf_p_values']
    return stats_data



def loss_function(params):
    
    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)
    
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    n_sim_log_price = n_stvol_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu21=params[1], mu22=params[2], mu31=params[3], mu41=params[4], mu42=params[5],  
        sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
        sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
        sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
        sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
        xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)
    
    n_sim_price = log_price_to_price(n_log_price=n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_return=n_sim_return, n_price=n_sim_price)


    for i in range(n_real_stats.shape[0]):
        for j in range(n_real_stats.shape[1]):
            moment_loss.iloc[i, j] = np.sqrt((n_real_stats.iloc[i, j] - n_sim_stats.iloc[i, j])**2)
    sum_all = np.sum(moment_loss)
    print(sum_all)
    print(np.sum(sum_all))
    print('----------')

    return np.sum(sum_all)



real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20180101_20181231/calibration_100_pairs_prices_2018.csv", 
                         index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20180101_20181231/calibration_100_pairs_returns_2018.csv", 
                          index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)


num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]

n_real_stats = real_stats




initial0 = [0.1, 1, 1, 0.1, 1, 1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1]

begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(None, None), (0, None), (0, None), (None, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)

 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1
[20] 0.1 0.1 0.1

450452
97804
return_mean1                      7.613139
return_mean2                      8.192020
return_sd1                      117.366248
return_sd2                      123.135646
return_skew1                     61.020371
return_skew2                     61.020371
return_kurtosis1                294.266361
return_kurtosis2                565.608165
return_autocorrelation1           7.787114
return_autocorrelation2           7.775691
return_correlation_ts1_lag_0     63.149932
return_correlation_ts1_lag_1      6.860181
return_correlation_ts1_lag_2      7.280375
return_correlation_ts1_lag_3      8.825743
return_correlation_ts2_lag_1      8.490779
return_correlation_ts2_lag_2      7.983891
return_correlation_ts2_lag_3      8.225499
price_adf_p_values               42.324760
dtype: float64
1406.9262860224935
----------
 [1] 0.1 1.0 1.0 0.1 1.0 1.0 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 

return_mean1                     11.027053
return_mean2                      8.292832
return_sd1                      116.077143
return_sd2                      121.850640
return_skew1                     56.690050
return_skew2                     56.690050
return_kurtosis1                289.799147
return_kurtosis2                567.038849
return_autocorrelation1           8.858553
return_autocorrelation2           9.358799
return_correlation_ts1_lag_0     63.151744
return_correlation_ts1_lag_1      8.312197
return_correlation_ts1_lag_2      8.022095
return_correlation_ts1_lag_3      9.203188
return_correlation_ts2_lag_1      9.632775
return_correlation_ts2_lag_2      8.544785
return_correlation_ts2_lag_3      9.251637
price_adf_p_values               24.954408
dtype: float64
1386.755944505469
----------
 [1] -0.3441239  1.0000000  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.1000000  0.1000000  0

return_mean1                     11.358549
return_mean2                      8.264325
return_sd1                      115.739594
return_sd2                      121.511798
return_skew1                     58.812269
return_skew2                     58.812269
return_kurtosis1                279.422726
return_kurtosis2                571.575417
return_autocorrelation1           8.804724
return_autocorrelation2           8.999158
return_correlation_ts1_lag_0     63.151240
return_correlation_ts1_lag_1      8.878611
return_correlation_ts1_lag_2      7.664067
return_correlation_ts1_lag_3      8.714976
return_correlation_ts2_lag_1      8.552921
return_correlation_ts2_lag_2      7.332366
return_correlation_ts2_lag_3      8.587216
price_adf_p_values               29.612701
dtype: float64
1385.794927875882
----------
 [1] -0.2375154  1.0000000  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.1000000  0.1000000  0

return_mean1                     12.688679
return_mean2                      8.200080
return_sd1                      113.121096
return_sd2                      124.851675
return_skew1                     59.093896
return_skew2                     59.093896
return_kurtosis1                284.457985
return_kurtosis2                550.958700
return_autocorrelation1           7.296822
return_autocorrelation2           6.616824
return_correlation_ts1_lag_0     63.131624
return_correlation_ts1_lag_1      7.834491
return_correlation_ts1_lag_2      8.183689
return_correlation_ts1_lag_3      7.835863
return_correlation_ts2_lag_1      7.679140
return_correlation_ts2_lag_2      8.192681
return_correlation_ts2_lag_3      7.396595
price_adf_p_values               32.310118
dtype: float64
1368.9438538581464
----------
 [1] -0.2366415  1.7935736  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.1000000  0.1000000  

return_mean1                     24.759025
return_mean2                      8.092585
return_sd1                       51.396697
return_sd2                      123.009475
return_skew1                     57.467899
return_skew2                     57.467899
return_kurtosis1                275.038658
return_kurtosis2                562.753786
return_autocorrelation1           8.696538
return_autocorrelation2           7.443956
return_correlation_ts1_lag_0     62.590742
return_correlation_ts1_lag_1      8.407647
return_correlation_ts1_lag_2      7.993114
return_correlation_ts1_lag_3      7.895352
return_correlation_ts2_lag_1      8.596625
return_correlation_ts2_lag_2      8.424527
return_correlation_ts2_lag_3      8.448034
price_adf_p_values               33.149797
dtype: float64
1321.6323559462535
----------
 [1] -0.2366415  2.2617025  1.0000000  0.1000000  1.0000000  1.0000000
 [7]  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000  0.1000000
[13]  0.1000000  0.1000000  0.1000000  

...

return_mean1                     18.277399
return_mean2                     72.365227
return_sd1                      107.994068
return_sd2                      446.652496
return_skew1                     61.961277
return_skew2                     61.961277
return_kurtosis1                307.262445
return_kurtosis2                559.134159
return_autocorrelation1           8.445823
return_autocorrelation2           8.539443
return_correlation_ts1_lag_0     37.450347
return_correlation_ts1_lag_1      7.669581
return_correlation_ts1_lag_2      7.844558
return_correlation_ts1_lag_3      7.941358
return_correlation_ts2_lag_1      8.417367
return_correlation_ts2_lag_2      8.955049
return_correlation_ts2_lag_3      8.903307
price_adf_p_values               24.124348
dtype: float64
1763.8995278710634
----------
 [1]  0.38139249  2.15476205  1.00784331 -0.56105894  1.56458134  0.83241641
 [7]  0.20995949  0.30131767  0.07644697  0.09297768  0.66302512  0.92688877
[13]  0.69994938  1.2432812

return_mean1                     19.502155
return_mean2                     72.942359
return_sd1                      123.956221
return_sd2                      488.125357
return_skew1                     58.792675
return_skew2                     58.792675
return_kurtosis1                282.779507
return_kurtosis2                505.085235
return_autocorrelation1           9.442396
return_autocorrelation2           9.789847
return_correlation_ts1_lag_0     39.214723
return_correlation_ts1_lag_1      8.661369
return_correlation_ts1_lag_2      8.315733
return_correlation_ts1_lag_3      7.608504
return_correlation_ts2_lag_1      9.301008
return_correlation_ts2_lag_2      8.863426
return_correlation_ts2_lag_3      8.332981
price_adf_p_values               25.421935
dtype: float64
1744.9281064728714
----------
 [1]  0.38139249  2.15476205  1.00784331 -0.56105894  1.56458134  0.83241641
 [7]  0.20995949  0.30131767  0.07644697  0.09297768  0.66302512  0.92688877
[13]  0.69994938  1.2432812

return_mean1                     21.346837
return_mean2                     73.728492
return_sd1                      128.402686
return_sd2                      470.274747
return_skew1                     60.787816
return_skew2                     60.787816
return_kurtosis1                321.153425
return_kurtosis2                536.117000
return_autocorrelation1           7.821703
return_autocorrelation2           8.162029
return_correlation_ts1_lag_0     38.706686
return_correlation_ts1_lag_1      8.173123
return_correlation_ts1_lag_2      9.077983
return_correlation_ts1_lag_3      8.509884
return_correlation_ts2_lag_1      8.238336
return_correlation_ts2_lag_2      8.831844
return_correlation_ts2_lag_3      8.359626
price_adf_p_values               24.088162
dtype: float64
1802.5681948939377
----------
 [1]  0.38139249  2.15476205  1.00784331 -0.56105894  1.56458134  0.83241641
 [7]  0.20995949  0.30131767  0.07644697  0.09297768  0.66302512  0.92688877
[13]  0.69994938  1.2432812

return_mean1                     23.753983
return_mean2                     80.106035
return_sd1                      144.915793
return_sd2                      514.933641
return_skew1                     61.132630
return_skew2                     61.132630
return_kurtosis1                313.648865
return_kurtosis2                560.562706
return_autocorrelation1           9.248940
return_autocorrelation2           9.368265
return_correlation_ts1_lag_0     40.278101
return_correlation_ts1_lag_1      8.566769
return_correlation_ts1_lag_2      9.989760
return_correlation_ts1_lag_3      8.064173
return_correlation_ts2_lag_1      9.358280
return_correlation_ts2_lag_2      8.384235
return_correlation_ts2_lag_3      7.703945
price_adf_p_values               27.245562
dtype: float64
1898.3943116548148
----------
 [1]  0.38139249  2.15476205  1.00784331 -0.56105894  1.56458134  0.83241641
 [7]  0.20995949  0.30131767  0.07644697  0.09297768  0.66302512  0.92688877
[13]  0.69994938  1.2432812

return_mean1                     21.492826
return_mean2                     75.706116
return_sd1                      148.550446
return_sd2                      531.578828
return_skew1                     59.511833
return_skew2                     59.511833
return_kurtosis1                314.420031
return_kurtosis2                594.969011
return_autocorrelation1           8.721284
return_autocorrelation2           8.950562
return_correlation_ts1_lag_0     41.823952
return_correlation_ts1_lag_1      8.168652
return_correlation_ts1_lag_2      9.958598
return_correlation_ts1_lag_3      8.885479
return_correlation_ts2_lag_1      8.567214
return_correlation_ts2_lag_2      8.606554
return_correlation_ts2_lag_3      8.760710
price_adf_p_values               29.827778
dtype: float64
1948.011706670743
----------
1948.011706670743


In [28]:
params = FloatVector(res.x)
print(params)
real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)

xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)


    
n_sim_log_prices = n_stvol_simulation(
    random_seed=9868, num_sim=248,
    mu11=params[0], mu21=params[1], mu22=params[2], 
    mu31=params[3], mu41=params[4], mu42=params[5],  
    sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
    sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
    sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
    sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
    xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250)

n_sim_pair_prices = log_price_to_price(n_log_price=n_sim_log_prices)
n_sim_pair_returns = price_to_return(n_price=n_sim_pair_prices)

print(n_sim_log_prices)
print(n_sim_pair_prices)
print(n_sim_pair_returns)

n_sim_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_prices.csv")
n_sim_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_returns.csv")


 [1]  0.38139249  2.15476205  1.00784331 -0.56105894  1.56458134  0.83241641
 [7]  0.20995949  0.30131767  0.07644697  0.09297768  0.66302512  0.92688877
[13]  0.69994938  1.24328127  0.27352879  0.40184367  0.45726440  0.26710722
[19]  1.14479443  1.60219186  0.46065129  1.99830672

          0         1         2         3         4         5         6    \
0    3.647595  4.134696  4.584573  4.021957  7.338973  5.094021  6.960993   
1    3.649350  4.133145  4.586149  4.020014  7.340805  5.092635  6.963122   
2    3.651388  4.130346  4.586880  4.017255  7.337453  5.080511  6.960857   
3    3.651042  4.126570  4.589148  4.014465  7.341453  5.078099  6.965684   
4    3.654339  4.133466  4.590582  4.010737  7.344994  5.087067  6.966565   
..        ...       ...       ...       ...       ...       ...       ...   
246  4.016870  2.682462  4.566493  2.615871  7.348411  3.804138  6.557509   
247  4.045693  2.709596  4.686836  2.942110  7.345661  3.772183  6.501644   
248  4.121103  2.78230

In [ ]:
random_seed=9868, num_sim=248,
mu11=0.26222544, mu21=2.96284705, mu22=2.79633061, 
mu31=-0.28927212, mu41=0.71695055, mu42=4.42044188,  
sigma11=0.26124088, sigma12=0.34270097, sigma13=0.24891787, sigma14=0.09048606,
sigma21=0.46810189, sigma22=0.70773396, sigma23=0.48192585, sigma24=0.81895315,
sigma31=0.76085335, sigma32=0.26146841, sigma33=0.62789311, sigma34=0.60658349,
sigma41=0.40349568, sigma42=0.59526509, sigma43=0.15285195, sigma44=0.55066164,
xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250

In [ ]:
stvol with 8

In [ ]:
import pandas as pd
import numpy as np
import random
from numpy.random import RandomState
from scipy import stats
from scipy.optimize import minimize
import scipy
import os
os.environ['R_HOME'] = '/Library/Frameworks/R.framework/Versions/4.1/Resources/'
import rpy2
from rpy2.robjects.packages import importr
from rpy2.robjects.packages import SignatureTranslatedAnonymousPackage
import datetime
from rpy2.robjects.vectors import FloatVector
from statsmodels.tsa.stattools import adfuller
from sklearn.linear_model import LinearRegression

rand_seed = 22101
np.random.seed(rand_seed)

yuima = importr("yuima")
n_stvol_sim_string = """
n_stvol = function(random_seed, num_sim,
                    mu11, mu21, mu22, mu31, mu41, mu42, 
                    sigma11, sigma12, sigma13, sigma14,
                    sigma21, sigma22, sigma23, sigma24,
                    sigma31, sigma32, sigma33, sigma34,
                    sigma41, sigma42, sigma43, sigma44,
                    xinit_vec, vinit_vec, T0, T, length){
  
  set.seed(random_seed)
  
  drift = c("mu11-(1/2)*(v1)^2", "mu21-mu22*v1", "mu31-(1/2)*(v2)^2", "mu41-mu42*v2")
  diffusion = matrix(c("sigma11*v1", "sigma12*v1", "sigma13*v1", "sigma14*v1", 
                       "sigma21", "sigma22", "sigma23", "sigma24", 
                       "sigma31*v2", "sigma32*v2", "sigma33*v2", "sigma34*v2", 
                       "sigma41", "sigma42", "sigma43", "sigma44"), 
                     4, 4, byrow=TRUE)
  
  stvol_model = setModel(drift=drift, diffusion=diffusion,
                          time.variable = "t",
                          state.variable=c("X1", "v1", "X2", "v2"),
                          solve.variable=c("X1", "v1", "X2", "v2"))
  newsamp = setSampling(Initial=T0, Terminal=T, n=length)
  
  n_sim_data = data.frame(matrix(nrow=length+1, ncol=2*num_sim))
  for (i in 1:num_sim){
    stvol_sim = simulate(stvol_model, 
                          true.par=list(
                            mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                            sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                            sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                            sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                            sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44), 
                          xinit=c(xinit_vec[[i]][1], vinit_vec[[i]][1], xinit_vec[[i]][2], vinit_vec[[i]][2]), 
                          sampling=newsamp)
    original_data = stvol_sim@data@original.data
    one_sim_stvol = data.frame(original_data[,1], original_data[,3])
    colnames(one_sim_stvol) = c('series1', 'series2')
    n_sim_data[, (2*i-1):(2*i)] = one_sim_stvol
  }
  return(n_sim_data)
}
"""

n_stvol_sim = SignatureTranslatedAnonymousPackage(n_stvol_sim_string, "n_stvol_sim")
def n_stvol_simulation(random_seed, num_sim,
                        mu11, mu21, mu22, mu31, mu41, mu42, 
                        sigma11, sigma12, sigma13, sigma14,
                        sigma21, sigma22, sigma23, sigma24,
                        sigma31, sigma32, sigma33, sigma34,
                        sigma41, sigma42, sigma43, sigma44,
                        xinit_vec, vinit_vec, T0, T, length):

    n_sim_data = pd.DataFrame(
        n_stvol_sim.n_stvol(random_seed=random_seed, num_sim=num_sim,
                              mu11=mu11, mu21=mu21, mu22=mu22, mu31=mu31, mu41=mu41, mu42=mu42,  
                              sigma11=sigma11, sigma12=sigma12, sigma13=sigma13, sigma14=sigma14,
                              sigma21=sigma21, sigma22=sigma22, sigma23=sigma23, sigma24=sigma24,
                              sigma31=sigma31, sigma32=sigma32, sigma33=sigma33, sigma34=sigma34,
                              sigma41=sigma41, sigma42=sigma42, sigma43=sigma43, sigma44=sigma44,
                              xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)).transpose()
    return n_sim_data


def price_to_log_price(n_price):
    return(np.log(n_price))

def log_price_to_price(n_log_price):
    return(np.exp(n_log_price))

def price_to_return(n_price):
    n_return = pd.DataFrame()
    for i in range(n_price.shape[1]):
        ith_column_price_series = n_price.iloc[:, i]
        n_return = pd.concat([n_return, 100 * (np.log(ith_column_price_series[1:].values) - np.log(ith_column_price_series[:-1]))], axis=1)
    return n_return

def log_price_to_return(n_log_price):
    n_real_return = pd.DataFrame()
    for i in range(n_log_price.shape[1]):
        ith_column_price_series = n_log_price.iloc[:, i]
        n_real_return = pd.concat([n_real_return, 100 * (ith_column_price_series[1:].values - ith_column_price_series[:-1])], axis=1)
    return n_real_return

def cross_corr_coef(lag_time_series, lead_time_series, lag):
    # calculate the cross correlation between two time series
    # if the result is not zero, then 'lead_time_series' leads 'lag_time_series'
    lag_time_series = lag_time_series.iloc[lag:]
    corr_coef = np.corrcoef(lag_time_series, lead_time_series.iloc[0:((lead_time_series.size)-lag)])[0][1]
    return corr_coef
    
def cal_stats(n_return, n_price):
    
    return_series1 = n_return.iloc[:, ::2]
    return_series2 = n_return.iloc[:, 1::2]
    price_series1 = n_price.iloc[:, ::2]
    price_series2 = n_price.iloc[:, 1::2]

    
    mean1 = return_series1.mean(axis=0).values
    sd1 = return_series1.std(axis=0).values
    skew1 = return_series1.skew(axis=0).values
    kurtosis1 = return_series1.kurtosis(axis=0).values
    autocorr1 = return_series1.apply(lambda x: x.autocorr(lag=1))    
    
    
    mean2 = return_series2.mean(axis=0).values
    sd2 = return_series2.std(axis=0).values
    skew2 = return_series1.skew(axis=0).values
    kurtosis2 = return_series2.kurtosis(axis=0).values
    autocorr2 = return_series2.apply(lambda x: x.autocorr(lag=1)) 
    
    
    # Cross-correlation between return series
    corr_ts1_lag_0 = []
    corr_ts1_lag_1 = [] # if not zero, return series 2 leads return series 1
    corr_ts1_lag_2 = []
    corr_ts1_lag_3 = []
    corr_ts2_lag_1 = [] # if not zero, return series 1 lead return series 2
    corr_ts2_lag_2 = []
    corr_ts2_lag_3 = []
    for i in range(248):
        corr_ts1_lag_0.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 0))
        corr_ts1_lag_1.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 1))
        corr_ts1_lag_2.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 2))
        corr_ts1_lag_3.append(cross_corr_coef(return_series1.iloc[:, i], return_series2.iloc[:, i], 3))
        corr_ts2_lag_1.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 1))
        corr_ts2_lag_2.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 2))
        corr_ts2_lag_3.append(cross_corr_coef(return_series2.iloc[:, i], return_series1.iloc[:, i], 3))
    corr_ts1_lag_0 = pd.Series(corr_ts1_lag_0)
    corr_ts1_lag_1 = pd.Series(corr_ts1_lag_1)
    corr_ts1_lag_2 = pd.Series(corr_ts1_lag_2)
    corr_ts1_lag_3 = pd.Series(corr_ts1_lag_3)
    corr_ts2_lag_1 = pd.Series(corr_ts2_lag_1)
    corr_ts2_lag_2 = pd.Series(corr_ts2_lag_2)
    corr_ts2_lag_3 = pd.Series(corr_ts2_lag_3)
    
    
    # adf test on original prices: test if the price difference of the two time series is stationary
    p_values = []
    for i in range(248):
        reg = LinearRegression().fit(np.array(price_series1.iloc[:, i]).reshape((-1, 1)), np.array(price_series2.iloc[:, i]))
        y_pred = reg.predict(np.array(price_series1.iloc[:, i]).reshape((-1, 1)))
        res = np.array(price_series2.iloc[:, i]) - y_pred
        adf_result = adfuller(res)[1]
        p_values.append(adf_result)
    p_values = pd.Series(p_values)
    
    
    stats_data = pd.DataFrame([mean1, mean2, sd1, sd2, 
                               skew1, skew2, kurtosis1, kurtosis2, 
                               autocorr1, autocorr2, corr_ts1_lag_0, 
                               corr_ts1_lag_1, corr_ts1_lag_2, corr_ts1_lag_3,
                               corr_ts2_lag_1, corr_ts2_lag_2, corr_ts2_lag_3,
                               p_values])
    stats_data = stats_data.transpose()
    stats_data.columns = [
        'return_mean1', 'return_mean2',
        'return_sd1', 'return_sd2',
        'return_skew1', 'return_skew2',
        'return_kurtosis1', 'return_kurtosis2',
        'return_autocorrelation1', 'return_autocorrelation2',
        'return_correlation_ts1_lag_0',
        'return_correlation_ts1_lag_1', 'return_correlation_ts1_lag_2', 'return_correlation_ts1_lag_3',
        'return_correlation_ts2_lag_1', 'return_correlation_ts2_lag_2', 'return_correlation_ts2_lag_3',
        'price_adf_p_values']
    return stats_data



def loss_function(params):
    
    params = FloatVector(params)
    print(params)
    moment_loss = pd.DataFrame().reindex_like(real_stats)
    
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    print(int(np.random.randint(low=0, high=980608, size=(1,))))
    n_sim_log_price = n_stvol_simulation(
        random_seed=int(np.random.randint(low=0, high=980608, size=(1,))), num_sim=num_sim,
        mu11=params[0], mu21=params[1], mu22=params[2], mu31=params[3], mu41=params[4], mu42=params[5],  
        sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
        sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
        sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
        sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
        xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=T0, T=T, length=length)
    
    n_sim_price = log_price_to_price(n_log_price=n_sim_log_price)
    n_sim_return = price_to_return(n_sim_price)
    n_sim_stats = cal_stats(n_return=n_sim_return, n_price=n_sim_price)


    for i in range(n_real_stats.shape[0]):
        for j in range(n_real_stats.shape[1]):
            moment_loss.iloc[i, j] = np.sqrt((n_real_stats.iloc[i, j] - n_sim_stats.iloc[i, j])**2)
    sum_all = np.sum(moment_loss)
    print(sum_all)
    print(np.sum(sum_all))
    print('----------')

    return np.sum(sum_all)



real_price = pd.read_csv("sp500_20180101_20181231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("sp500_20180101_20181231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)


xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)


num_sim, T0, T, length = real_stats.shape[0], 0, 1, real_price.shape[0]

n_real_stats = real_stats




initial0 = [0.1, 1, 1, 0.1, 1, 1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1,
            0.1, 0.1, 0.1, 0.1]

begin_time = datetime.datetime.now()
res = minimize(loss_function, initial0, method='Powell',
               tol=1e-6, options={'disp': True},
               bounds=[(None, None), (None, None), (None, None), (None, None), (None, None), (None, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None),
                       (0, None), (0, None), (0, None), (0, None)])
print(res.x)

time = datetime.datetime.now() - begin_time
print(time)

params = (res.x)
loss = loss_function((params))
print(loss)

In [32]:
params = FloatVector((-0.092325, 
           0.614664,
           1.652460,
          -0.075268,
           0.635211,
           1.344474,
        0.188204,
        0.189660,
        0.172057,
        0.132407,
        0.248200,
        0.220798,
        0.292431,
        0.332290,
        0.220722,
        0.199752,
        0.220673,
        0.210290,
        0.341082,
        0.378990,
        0.230360,
      0.292098))

In [2]:
params = FloatVector((
-9.23250475e-02,  6.14663604e-01,  1.65246006e+00, -7.52679813e-02,
        6.35211085e-01,  1.34447368e+00,  1.88204013e-01,  1.89660428e-01,
        1.72056648e-01,  1.32406669e-01,  2.48199905e-01,  2.20798299e-01,
        2.92431187e-01,  3.32289663e-01,  2.20722161e-01,  1.99751608e-01,
        2.20672834e-01,  2.10289787e-01,  3.41081793e-01,  3.78989899e-01,
        2.30359901e-01,  2.92097749e-01,  2.30256875e+04,  4.13574460e+03))

In [9]:

print(params)
real_price = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_prices.csv", index_col=[0])
real_log_price = price_to_log_price(n_price=real_price)
real_return = pd.read_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Data/sp500_20190101_20191231/sp500_20190101_20191231_pair_returns.csv", index_col=[0])
real_stats = cal_stats(n_return=real_return, n_price=real_price)

xinit_vec = []
vinit_vec = []
for i in range(int(real_price.shape[1]/2)):

    init_pair_log_price = [real_log_price.iloc[0, 2*i], real_log_price.iloc[0, 2*i+1]]
    init_pair_log_price = FloatVector(init_pair_log_price)
    xinit_vec.append(init_pair_log_price)
    
    init_pair_volatility = [np.std(real_return.iloc[:, 2*i]/100), np.std(real_return.iloc[:, 2*i+1]/100)]
    init_pair_volatility = FloatVector(init_pair_volatility)
    vinit_vec.append(init_pair_volatility)


    
n_sim_log_prices = n_stvol_simulation(
    random_seed=9868, num_sim=248,
    mu11=params[0], mu21=params[1], mu22=params[2], 
    mu31=params[3], mu41=params[4], mu42=params[5],  
    sigma11=params[6], sigma12=params[7], sigma13=params[8], sigma14=params[9],
    sigma21=params[10], sigma22=params[11], sigma23=params[12], sigma24=params[13],
    sigma31=params[14], sigma32=params[15], sigma33=params[16], sigma34=params[17],
    sigma41=params[18], sigma42=params[19], sigma43=params[20], sigma44=params[21],
    xinit_vec=xinit_vec, vinit_vec=vinit_vec, T0=0, T=1, length=250)

n_sim_pair_prices = log_price_to_price(n_log_price=n_sim_log_prices)
n_sim_pair_returns = price_to_return(n_price=n_sim_pair_prices)

print(n_sim_log_prices)
print(n_sim_pair_prices)
print(n_sim_pair_returns)

n_sim_pair_prices.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_prices.csv")
n_sim_pair_returns.to_csv("/Users/changmao/Desktop/OneDrive - Imperial College London/InferStat - MSc Summer Project/GitHub/Summer-Research-Project/Calibration/Cluster jobs/stvol1998/n_sim_pair_returns.csv")


 [1] -9.232505e-02  6.146636e-01  1.652460e+00 -7.526798e-02  6.352111e-01
 [6]  1.344474e+00  1.882040e-01  1.896604e-01  1.720566e-01  1.324067e-01
[11]  2.481999e-01  2.207983e-01  2.924312e-01  3.322897e-01  2.207222e-01
[16]  1.997516e-01  2.206728e-01  2.102898e-01  3.410818e-01  3.789899e-01
[21]  2.303599e-01  2.920977e-01  2.302569e+04  4.135745e+03

          0         1         2         3         4         5         6    \
0    3.647595  4.134696  4.584573  4.021957  7.338973  5.094021  6.960993   
1    3.647496  4.134710  4.584378  4.021907  7.339049  5.094252  6.961215   
2    3.647516  4.134836  4.583184  4.020710  7.336758  5.091882  6.960002   
3    3.646183  4.132804  4.582782  4.020410  7.336563  5.091543  6.959385   
4    3.645428  4.131841  4.582588  4.020007  7.337080  5.092854  6.958596   
..        ...       ...       ...       ...       ...       ...       ...   
246  3.573084  4.025628  4.462976  3.889332  7.175348  4.864460  6.758357   
247  3.576997  4.03025